# How to Register and Deploy Mistral NeMo Instruct-2407 with Hopsworks 

### Install HuggingFace Hub library

We will download the Mistral model files (e.g., weights, configuration files) directly from the HuggingFace repository

In [1]:
!pip install huggingface_hub --quiet

In [1]:
# Place your HuggingFace token in the HF_TOKEN environment variable

import os
os.environ["HF_TOKEN"] = "<INSERT_HF_TOKEN_HERE>"

In [3]:
from huggingface_hub import snapshot_download

import time
start_time = time.perf_counter()

# mistral_nemo_local_dir = snapshot_download("mistralai/Mistral-NeMo-Instruct-2407", allow_patterns=["params.json", "consolidated.safetensors", "tekken.json"])
mistral_nemo_local_dir = snapshot_download("mistralai/Mistral-NeMo-Instruct-2407", ignore_patterns=["model-00001-of-00005.safetensors", "model-00002-of-00005.safetensors", "model-00003-of-00005.safetensors", "model-00004-of-00005.safetensors", "model-00005-of-00005.safetensors"])

end_time = time.perf_counter()
print(f"\n... execution time: {end_time - start_time:.6f} seconds")

Fetching 13 files:   0%|          | 0/13 [00:00<?, ?it/s]

config.json:   0%|          | 0.00/622 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.5k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/3.13M [00:00<?, ?B/s]

.gitattributes:   0%|          | 0.00/1.57k [00:00<?, ?B/s]

...

special_tokens_map.json:   0%|          | 0.00/414 [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.26M [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/2.47M [00:00<?, ?B/s]

tekken.json:   0%|          | 0.00/14.8M [00:00<?, ?B/s]


... execution time: 598.836902 seconds


In [4]:
os.listdir(mistral_nemo_local_dir)

['special_tokens_map.json',
 'merges.txt',
 'tekken.json',
 'params.json',
 '.gitattributes',
 'consolidated.safetensors',
 'README.md',
 'config.json',
 'tokenizer.json',
 'tokenizer_config.json',
 'vocab.json',
 'generation_config.json',
 'model.safetensors.index.json']

## Register Mistral NeMo Instruct-2407 into Hopsworks Model Registry

In [2]:
import hopsworks

project = hopsworks.login()
mr = project.get_model_registry()

2024-12-13 13:03:10,102 INFO: Python Engine initialized.

Logged in to project, explore it here https://hopsworks.ai.local/p/119


In [6]:
hw_llm = mr.llm.create_model(name="mistral_nemo_instruct", description="Mistral NeMo Instruct-2407 model (via HF)")

In [7]:
import time

start_time = time.perf_counter()

hw_llm.save(mistral_nemo_local_dir)

end_time = time.perf_counter()
print(f"\n... execution time: {end_time - start_time:.6f} seconds")

  0%|          | 0/6 [00:00<?, ?it/s]

Model created, explore it at https://hopsworks.ai.local/p/119/models/mistral_nemo_instruct/1

... execution time: 450.999662 seconds


## Deploy Mistral NeMo

In [3]:
hw_llm = mr.get_model("mistral_nemo_instruct")

2024-12-13 13:03:10,351 WARNING: VersionWarning: No version provided for getting model `mistral_nemo_instruct`, defaulting to `1`.



In [5]:
deployment = hw_llm.deploy(
    name="mistralnemoinstructtools",
    description="Mistral NeMo Instruct-2407 from HuggingFace (with Tools)", 
    script_file="/Projects/ericsson/Jupyter/mistral_example/mistral_predictor.py",
    resources={"num_instances": 1, "requests": {"cores": 3, "memory": 1024*18, "gpus": 1}},
)

Deployment created, explore it at https://hopsworks.ai.local/p/119/deployments/14
Before making predictions, start the deployment by using `.start()`


In [6]:
deployment.start(await_running=60*15) # wait for 15 minutes maximum

  0%|          | 0/5 [00:00<?, ?it/s]

Start making predictions by using `.predict()`


In [31]:
# deployment.stop()
# deployment.delete()

In [32]:
# ms = project.get_model_serving()
# deployment = ms.get_deployment("mistralnemoinstruct")

In [ ]:
deployment.get_state().describe()

## Prompting Mistral NeMo

### Using httpx

In [7]:
import httpx

istio_endpoint = "http://51.89.118.251"

completions_url = istio_endpoint + "/openai/v1/completions"
chat_completions_url = istio_endpoint + "/openai/v1/chat/completions"

api_key_value = "qD9LAqy47KOnD9XK.AWniYJpuvSd73XCNgSzPnrWpNIcLtnYHjujerOqoK8xhMXEQmW1eSjqDcx85hmfH"
host_header = f"{deployment.name}.{project.name}.hopsworks.ai"

headers = {
    'Content-Type': 'application/json',
    'Authorization': 'ApiKey ' + api_key_value,
    'Host': host_header,
}

In [8]:
#
# Completion for a single prompt
#

user_message = "Who is the best French painter. Answer with detailed explanations."

# Mistral requires the following template
prompt = f"<s>[INST]{user_message}[/INST]"

data = {
    "model": deployment.name,
    "prompt": prompt,
    "max_tokens": 20234,
}

response = httpx.post(completions_url, headers=headers, json=data, timeout=45.0)
# print(response)
print(response.json()["choices"][0]["text"])

2024-12-13 13:09:24,396 INFO: HTTP Request: POST http://51.89.118.251/openai/v1/completions "HTTP/1.1 200 OK"
 The best French painter is often considered to be Claude Monet (1840-1926), one of the founders of French Impressionist painting. Here are a few reasons why:

1. **Impressionism**: Monet is credited with initiating the Impressionist movement. He developed a painting technique that shaded forms with patterns of small, visible brush strokes, which blended optically from a distance. This methodological innovation had a profound impact on art history.

2. **Water Lilies (Nymphéas)**: Monet's extensive series of approximately 250 oil paintings, all depicting various scenes of his water lily pond in Giverny, is his most renowned work. These paintings are celebrated for their vivid capturing of atmospheric changes and perpetual movement, reflecting the artist's deep engagement with nature.

3. **Cultural Influence**: Monet's works had a significant influence on many other painters, b

In [9]:
#
# Chat Completion for a user message
#

user_message = "Who is the best French painter. Answer with detailed explanations."

data = {
    "model": deployment.name,
    "messages": [
        {
            "role": "user",
            "content": user_message
        }
    ]
}

response = httpx.post(chat_completions_url, headers=headers, json=data, timeout=45.0)
print(response.json()["choices"][0]["message"]["content"])

2024-12-13 13:09:37,250 INFO: HTTP Request: POST http://51.89.118.251/openai/v1/chat/completions "HTTP/1.1 200 OK"
The title of "best French painter" is subjective and depends on personal preferences, but two names often cited in such discussions are Pablo Picasso and Claude Monet. Here's why:

1. **Pablo Picasso (1881-1973)**: Many consider Picasso the best painter of all time, not just the best French painter. His influence on the art world is immeasurable, and his roles in developing Cubism and Neoclassicism make him a clear choice for many. Picasso's early work shows prodigious talent, and his later works are diverse and innovative, reflecting his constant evolution as an artist. His Mona Lisa-with-fangs provides a great example of his unique approach to art.

2. **Claude Monet (1840-1926)**: As the father of French Impressionism, Monet had a tremendous impact on art history. His innovative techniques, such as painting en plein air (outdoors) and focusing on the accurate depiction 

# Using OpenAI client

In [10]:
!pip install openai --quiet

In [11]:
from openai import OpenAI

In [12]:
client = OpenAI(
    base_url="http://51.89.118.251/openai/v1",
    api_key="X",
    default_headers={
        "Authorization": "ApiKey qD9LAqy47KOnD9XK.AWniYJpuvSd73XCNgSzPnrWpNIcLtnYHjujerOqoK8xhMXEQmW1eSjqDcx85hmfH",
        "Host": f"{deployment.name}.{project.name}.hopsworks.ai",
    }
)

In [13]:
user_message = "Who is the best French painter. Answer with detailed explanations."

# Mistral requires the following template
prompt = f"<s>[INST]{user_message}[/INST]"

chat_response = client.completions.create(
    model=deployment.name,
    prompt=prompt,
)
print(chat_response.choices[0].text)

2024-12-13 13:09:40,864 INFO: HTTP Request: POST http://51.89.118.251/openai/v1/completions "HTTP/1.1 200 OK"
The title of the best French painter is often given to two artists whose works have


In [14]:
chat_response = client.chat.completions.create(
    model=deployment.name,
    messages=[
        {"role": "user", "content": "Who is the best French painter. Answer with detailed explanations."},
    ]
)
print(chat_response.choices[0].message.content)

2024-12-13 13:09:58,758 INFO: HTTP Request: POST http://51.89.118.251/openai/v1/chat/completions "HTTP/1.1 200 OK"
 The term "best" can be subjective and depends on personal preference, but French painting has produced many renowned artists. Here, I'll discuss two of the most influential and celebrated French painters, Claude Monet and Pablo Picasso, focusing on their significant contributions and unique styles.

1. **Claude Monet (1840-1926)**
   - **Impressionism**: Monet is considered the father of Impressionism, a 19th-century art movement that emphasized accurate depiction of light and its changing qualities. Impressionist artists often painted en plein air (outdoors) to capture fleeting moments and effects of light and atmosphere.
   - **Works**: Monet's works include iconic series such as "Impression, Sunrise," "Water Lilies," and "Haystacks." He painted these subjects multiple times at different hours of the day, seasons, and weather conditions, showcasing his mastery of captur